In [ ]:
%matplotlib inline


# Scalable problem

We want to solve the Aerostructure MDO problem
by means of the :class:`.MDF` formulation
with a higher dimension for the sweep parameter.
For that, we use the :class:`.ScalableProblem` class.


In [ ]:
from __future__ import division, unicode_literals

from gemseo.api import configure_logger, create_discipline, create_scenario
from gemseo.problems.aerostructure.aerostructure_design_space import (
    AerostructureDesignSpace,
)
from gemseo.problems.scalable.data_driven.problem import ScalableProblem

configure_logger()

## Define the design problem
In a first step, we define the design problem in terms of
objective function (to maximize or minimize),
design variables (local and global)
and constraints (equality and inequality).



In [ ]:
design_variables = ["thick_airfoils", "thick_panels", "sweep"]
objective_function = "range"
eq_constraints = ["c_rf"]
ineq_constraints = ["c_lift"]
maximize_objective = True

## Create the disciplinary datasets
Then, we create the disciplinary :class:`.AbstractFullCache` datasets
based on a :class:`.DiagonalDOE`.



In [ ]:
disciplines = create_discipline(["Aerodynamics", "Structure", "Mission"])
for discipline in disciplines:
    discipline.set_cache_policy(discipline.MEMORY_FULL_CACHE)
    design_space = AerostructureDesignSpace()
    design_space.filter(discipline.get_input_data_names())
    output = next(iter(discipline.get_output_data_names()))
    scenario = create_scenario(
        discipline, "DisciplinaryOpt", output, design_space, scenario_type="DOE"
    )
    scenario.execute({"algo": "DiagonalDOE", "n_samples": 10})

## Instantiate a scalable problem
In a third stage, we instantiate a :class:`.ScalableProblem`
from these disciplinary datasets and from the definition of the MDO problem.
We also increase the dimension of the sweep parameter.



In [ ]:
datasets = [discipline.cache.export_to_dataset() for discipline in disciplines]
problem = ScalableProblem(
    datasets,
    design_variables,
    objective_function,
    eq_constraints,
    ineq_constraints,
    maximize_objective,
    sizes={"sweep": 2},
)
print(problem)

<div class="alert alert-info"><h4>Note</h4><p>We could also provide options to the :class:`.ScalableModel` objects
   by means of the constructor of :class:`.ScalableProblem`,
   e.g. :code:`fill_factor` in the frame of the :class:`.ScalableDiagonalModel`.
   In this example, we use the standard ones.</p></div>



## Visualize the N2 chart
We can see the coupling between disciplines through this N2 chart:



In [ ]:
problem.plot_n2_chart(save=False, show=True)

## Create an MDO scenario
Lastly, we create a :class:`.MDOScenario` with the :class:`.MDF` formulation
and start the optimization at equilibrium,
thus ensuring the feasibility of the first iterate.



In [ ]:
scenario = problem.create_scenario("MDF", start_at_equilibrium=True)

<div class="alert alert-info"><h4>Note</h4><p>We could also provide options for the scalable models to the constructor
   of :class:`.ScalableProblem`, e.g. :code:`fill_factor` in the frame of
   the :class:`.ScalableDiagonalModel`.
   In this example, we use the standard ones.</p></div>



Once the scenario is created, we can execute it as any scenario.
Here, we use the :code:`NLOPT_SLSQP` optimization algorithm
with no more than 100 iterations.



In [ ]:
scenario.execute({"algo": "NLOPT_SLSQP", "max_iter": 100})

We can post-process the results.
Here, we use the standard :class:`.OptHistoryView`.



In [ ]:
scenario.post_process("OptHistoryView", save=False, show=True)